In [1]:
import wandb
import os
import pickle
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd


def get_history(user="anon", project="anon", query={},
                **kwargs):
    api = wandb.Api()
    runs = api.runs(path=f"{user}/{project}", filters=query)
    dataframes = [run.history(**kwargs) for run in runs]
    if len(runs) == 0:
        return [[],[]]
    else:
        return list(zip(runs, dataframes))


def download_files(user="anon", project="anon",
                   query={}, save_dir=".", **kwargs):
    """
    Download the files of each run into a new directory for the run.
    Also saves the config dict of the run.
    """
    if not os.path.isdir(save_dir):
        os.mkdir(save_dir)

    api = wandb.Api()
    runs = api.runs(path=f"{user}/{project}", filters=query)
    for run in runs:
        name = run.name
        config = run.config

        run_dir = os.path.join(save_dir, name)
        if not os.path.isdir(run_dir):
            os.mkdir(run_dir)

        with open(os.path.join(run_dir, "config.pkl"), "wb") as h:
            pickle.dump(config, h)

        files = run.files()
        for file in files:
            file.download(root=run_dir)
    return

In [2]:
from pytorch_lightning import Trainer
from pl_trainer import DynamicsModel, SaveTestLogCallback
import os

def load_model_from_run(run, save_dir="/tmp"):
    name = run.display_name
    ckpt_save_path = os.path.join(save_dir, name)
    if not os.path.exists(ckpt_save_path):
        os.makedirs(ckpt_save_path)
     
    ckpts = sorted([f for f in run.files() if "checkpoints" in f.name])
    if len(ckpts) == 0:
        raise RuntimeError(f"Run {name} has no checkpoints!")
    # pick latest checkpoint if available
    last_ckpt = ckpts[-1]
    last_ckpt.download(replace=True, root=ckpt_save_path)
        
    ckpt_path = os.path.join(ckpt_save_path, last_ckpt.name)
    # Uncommet if you need the trainer
    pl_trainer = Trainer(resume_from_checkpoint=ckpt_path,logger=False)
    pl_model = DynamicsModel.load_from_checkpoint(ckpt_path)
    
    import pprint 
    pp = pprint.PrettyPrinter(indent=4)
    print("--------------------------------")
    print("Model Hyperparameters:")
    pp.pprint(vars(pl_model.hparams))
    print("--------------------------------")
    return pl_trainer, pl_model

def load_file_from_run(run, filename, save_dir="/tmp", replace=False):
    name = run.display_name
    save_path = os.path.join(save_dir, name)
    if not os.path.exists(save_path):
        os.makedirs(save_path)
    for f in run.files():
        if filename in f.name:
            file_path = os.path.join(save_path, f.name)
            if not os.path.exists(file_path):
                f.download(replace=replace, root=save_path)
            else:
                print("File already exists")
            return file_path
    raise ValueError("File not found in run!")

In [3]:
# See https://docs.wandb.com/library/reference/wandb_api for how to write queries

# Best trials
query = {"$and": 
             [{"$or": [
                 {"displayName": {"$in": ["brisk-flower-430", # NN on Rotor
                                 "quiet-night-429", #CLNN on Rotor
                                 "fragrant-pine-365", #CHNN on Rotor
                                 "sunny-feather-366", # HNN on Rotor died from NaNs
                                 "rosy-shadow-436", # LNN on Rotor stuck
                                 "magic-frost-437", # NN on Gyroscope   
                                 "gallant-durian-439", # CHNN on Gyroscope
                                 "super-vortex-440", # CLNN on Gyroscope
                                ]}},
                 {"$and": [{"tags": "data-efficiency"}, {"config.n_train": 800}]}]},
              {"state": "finished"},
              {"config.network_class": {"$ne": "LNN"}},
             ]
}


runs, histories = zip(*get_history(query=query))

In [4]:
#trainers = []
#for run in runs:
#    trainer, pl_model = load_model_from_run(run)
#    trainer.model = pl_model
    
#    trainers.append(trainer)
    
#for trainer in trainers:
#    trainer.test()

In [5]:
import torch

labels = []
series = []

for run in runs:
    trainer, pl_model = load_model_from_run(run)
    pl_model.body.to(dtype=torch.float32)

    test_log_path = load_file_from_run(run, "test_log.pt")
    test_log = torch.load(test_log_path)

    pred_zts = test_log["pred_zts"].to(torch.float32)
    true_zts = test_log["true_zts"].to(torch.float32)
    pert_zts = test_log["pert_zts"].to(torch.float32)

    body_args = tuple(run.config["body_args"])
    if len(body_args) == 0:
        body_args = ""
    elif len(body_args) == 1:
        body_args = f"({body_args[0]})"
    else:
        body_args = f"{body_args}"
    body = f"{run.config['body_class']}{body_args}"
    network_class = run.config["network_class"]

    true_energy_pred = pl_model.true_energy(pred_zts)
    true_energy_true = pl_model.true_energy(true_zts)
    true_energy_pert = pl_model.true_energy(pert_zts)
    
    true_energy_rel_diff_pred_true = (true_energy_pred - true_energy_true).div(true_energy_pred + true_energy_true).abs().cpu().numpy()
    #true_energy_diff_pert_true = true_energy_pert - true_energy_true

    series += true_energy_rel_diff_pred_true.tolist()
    labels += [(body, network_class, "true_energy_rel_diff_pred_true", i) for i in range(len(true_energy_rel_diff_pred_true))]

    #series += true_energy_true.tolist()
    #labels += [(body, network_class, "true_energy_true", i) for i in range(len(true_energy_true))]
    
    #series += true_energy_pert.tolist()
    #labels += [(body, network_class, "true_energy_pert", i) for i in range(len(true_energy_pert))]

INFO:lightning:GPU available: True, used: False
/home/anon/miniconda3/envs/ham37v2/lib/python3.7/site-packages/torch/serialization.py:657: SourceChangeWarning: source code of class 'pl_trainer.DynamicsModel' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/home/anon/miniconda3/envs/ham37v2/lib/python3.7/site-packages/torch/serialization.py:657: SourceChangeWarning: source code of class 'torch.nn.modules.linear.Linear' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/home/anon/miniconda3/envs/ham37v2/lib/python3.7/site-packages/torch/serialization.py:657: SourceChangeWarning: source code of class 'torch.nn.modules.activation.Ta

CH ignores angular_dims
CH currently assumes potential energy depends only on q
CH currently assumes time independent Hamiltonian
CH assumes positions q are in Cartesian coordinates
--------------------------------
Model Hyperparameters:
{   'angular_dims': range(0, 5),
    'batch_size': 800,
    'body_args': [5],
    'body_class': 'ChainPendulum',
    'callbacks': [   <pytorch_lightning.callbacks.lr_logger.LearningRateLogger object at 0x7f2450f9f390>,
    'check_val_every_n_epoch': 100,
    'chunk_len': 5,
    'ckpt_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn5m1l1/CHNN/wandb/run-20200506_222109-2d3zj9wh/anon/version_2d3zj9wh/checkpoints',
    'dataset_class': 'RigidBodyDataset',
    'debug': False,
    'dof_ndim': 2,
    'dt': 0.1,
    'euclidean': True,
    'exp_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn5m1l1/CHNN',
    'fast_dev_run': False,
    'gpus': 1,
    'hidden_size': 200,
    'integration_time': 10.0,
    'logger': <pytorc

INFO:lightning:GPU available: True, used: False


CH ignores angular_dims
CH currently assumes potential energy depends only on q
CH currently assumes time independent Hamiltonian
CH assumes positions q are in Cartesian coordinates
--------------------------------
Model Hyperparameters:
{   'angular_dims': range(0, 3),
    'batch_size': 800,
    'body_args': [3],
    'body_class': 'ChainPendulum',
    'callbacks': [   <pytorch_lightning.callbacks.lr_logger.LearningRateLogger object at 0x7f2450fb2950>,
    'check_val_every_n_epoch': 100,
    'chunk_len': 5,
    'ckpt_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn3m1l1/CHNN/wandb/run-20200506_184402-3qfqmpge/anon/version_3qfqmpge/checkpoints',
    'dataset_class': 'RigidBodyDataset',
    'debug': False,
    'dof_ndim': 2,
    'dt': 0.1,
    'euclidean': True,
    'exp_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn3m1l1/CHNN',
    'fast_dev_run': False,
    'gpus': 1,
    'hidden_size': 200,
    'integration_time': 10.0,
    'logger': <pytorc

INFO:lightning:GPU available: True, used: False
/home/anon/miniconda3/envs/ham37v2/lib/python3.7/site-packages/torch/serialization.py:657: SourceChangeWarning: source code of class 'torch.nn.modules.container.ParameterDict' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)


...

CH ignores angular_dims
CH currently assumes potential energy depends only on q
CH currently assumes time independent Hamiltonian
CH assumes positions q are in Cartesian coordinates
--------------------------------
Model Hyperparameters:
{   'angular_dims': range(0, 1),
    'batch_size': 800,
    'body_args': [1],
    'body_class': 'ChainPendulum',
    'callbacks': [   <pytorch_lightning.callbacks.lr_logger.LearningRateLogger object at 0x7f244936f150>,
    'check_val_every_n_epoch': 100,
    'chunk_len': 5,
    'ckpt_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn1m1l1/CLNN/wandb/run-20200506_062510-2ty9ad4n/anon/version_2ty9ad4n/checkpoints',
    'dataset_class': 'RigidBodyDataset',
    'debug': False,
    'dof_ndim': 2,
    'dt': 0.1,
    'euclidean': True,
    'exp_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn1m1l1/CLNN',
    'fast_dev_run': False,
    'gpus': 1,
    'hidden_size': 200,
    'integration_time': 10.0,
    'logger': <pytorc

INFO:lightning:GPU available: True, used: False


tensor(0.0817, dtype=torch.float64)
NN ignores wgrad
NN currently assumes time independent ODE
--------------------------------
Model Hyperparameters:
{   'angular_dims': range(0, 1),
    'batch_size': 800,
    'body_args': [1],
    'body_class': 'ChainPendulum',
    'callbacks': [   <pytorch_lightning.callbacks.lr_logger.LearningRateLogger object at 0x7f24494e2a10>,
    'check_val_every_n_epoch': 100,
    'chunk_len': 5,
    'ckpt_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn1m1l1/NN/wandb/run-20200506_055600-2hu4osjq/anon/version_2hu4osjq/checkpoints',
    'dataset_class': 'RigidBodyDataset',
    'debug': False,
    'dof_ndim': 1,
    'dt': 0.1,
    'euclidean': False,
    'exp_dir': '/home/anon/repos/hamiltonian-biases/experiments/ChainPendulumn1m1l1/NN',
    'fast_dev_run': False,
    'gpus': 1,
    'hidden_size': 200,
    'integration_time': 10.0,
    'logger': <pytorch_lightning.loggers.wandb.WandbLogger object at 0x7f24492d6d50>,
    'lr': 0.01,
    'max_

INFO:lightning:GPU available: True, used: False


CH ignores angular_dims
CH currently assumes potential energy depends only on q
CH currently assumes time independent Hamiltonian
CH assumes positions q are in Cartesian coordinates
--------------------------------
Model Hyperparameters:
{   'angular_dims': range(3, 6),
    'batch_size': 800,
    'body_args': [],
    'body_class': 'Rotor',
    'callbacks': [   <pytorch_lightning.callbacks.lr_logger.LearningRateLogger object at 0x7f2448fb7910>,
    'check_val_every_n_epoch': 100,
    'chunk_len': 5,
    'ckpt_dir': '/home/anon/repos/hamiltonian-biases/experiments/Rotor/CHNN/wandb/run-20200506_054655-36ekb2wo/anon/version_36ekb2wo/checkpoints',
    'dataset_class': 'RigidBodyDataset',
    'debug': False,
    'dof_ndim': 3,
    'dt': 0.1,
    'euclidean': True,
    'exp_dir': '/home/anon/repos/hamiltonian-biases/experiments/Rotor/CHNN',
    'fast_dev_run': False,
    'gpus': 1,
    'hidden_size': 200,
    'integration_time': 10.0,
    'logger': <pytorch_lightning.loggers.wandb.WandbLogger

In [6]:
#index = pd.MultiIndex.from_tuples(labels, names =('Body', 'Network', "Series"))
index = pd.MultiIndex.from_tuples(labels, names =('Body', 'Network', "Series", "Batch"))
df = pd.DataFrame(series, index=index).T

In [7]:
dt = run.config["dt"]
integration_time = run.config["integration_time"]
chunk_len = run.config["chunk_len"] * dt

In [8]:
time = pd.Series(np.arange(0, integration_time, dt))
df.index = time

In [9]:
df.head()

Body                  ChainPendulum(5)                                \
Network                           CHNN                                 
Series  true_energy_rel_diff_pred_true                                 
Batch                               0         1         2         3    
0.0                           0.000000  0.000000  0.000000  0.000000   
0.1                           0.000616  0.000758  0.002991  0.000428   
0.2                           0.001990  0.001496  0.000661  0.001380   
0.3                           0.003582  0.002007  0.001819  0.002534   
0.4                           0.004463  0.002127  0.000427  0.003555   

Body                                                                 ...  \
Network                                                              ...   
Series                                                               ...   
Batch          4         5         6         7         8         9   ...   
0.0      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  ...   
0.1      0.000199  0.002815  0.000044  0.014137  0.010963  0.001763  ...   
0.2      0.003261  0.000556  0.000039  0.020344  0.014496  0.002546  ...   
0.3      0.007813  0.008007  0.000048  0.016868  0.019836  0.003074  ...   
0.4      0.008226  0.010211  0.000361  0.023677  0.029504  0.003212  ...   

Body                             Rotor                                \
Network                           CHNN                                 
Series  true_energy_rel_diff_pred_true                                 
Batch                               90        91        92        93   
0.0                           0.000000  0.000000  0.000000  0.000000   
0.1                           0.000031  0.000019  0.000008  0.000008   
0.2                           0.000063  0.000041  0.000017  0.000015   
0.3                           0.000095  0.000062  0.000024  0.000019   
0.4                           0.000127  0.000085  0.000031  0.000018   

Body                                                                 
Network                                                              
Series                                                               
Batch          94        95        96        97        98        99  
0.0      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
0.1      0.000004  0.000126  0.000182  0.000014  0.000050  0.000010  
0.2      0.000007  0.000243  0.000342  0.000026  0.000099  0.000023  
0.3      0.000009  0.000344  0.000469  0.000036  0.000148  0.000037  
0.4      0.000010  0.000427  0.000558  0.000043  0.000194  0.000052  

[5 rows x 2200 columns]

In [10]:
df = df.sort_index(axis=1, level="Body", ascending=True)

In [11]:
sns.set(font_scale=1.25)
sns.set_style('whitegrid')
sns.set_palette(sns.color_palette("Set1", n_colors=6, desat=.67))
import matplotlib as mpl
mpl.rcParams['figure.dpi'] = 1000

In [19]:
df_batch_avg = df.T.groupby(level=("Body", "Network", "Series")).mean().T
#df_batch_avg = df_batch_avg.T.swaplevel("Body", "Network").drop("NN").swaplevel("Network", "Body").T
n_systems = len(df.columns.unique("Body"))
n_networks = len(df.columns.unique("Network"))

# TODO: uncomment when more than 1 system
#fig, axes = plt.subplots(ncols=n_systems, figsize=(4 * n_systems, 4))
fig, axes = plt.subplots(ncols=3, nrows=2, figsize=(4 * 3, 4 *2))
#fig, axes = plt.subplots(ncols=2, figsize=(4 * 2, 4))

for system, ax in zip(df.columns.unique("Body"), axes.flatten()):
    df_batch_avg.loc[:, (system, slice(None), "true_energy_rel_diff_pred_true")].plot(ax=ax, linewidth=2.5)
    ax.set(title=system,
           #xlabel=f"Forward prediction (seconds)",
           yscale="log",
           #ylim=(1e-5, 2),
          )
    
    # Just take the perturbation curve from NN
    #df_batch_avg.loc[:, (system, "NN", "true_energy_pred")].plot(ax=ax, linewidth=2.5)
    
    ax.axvline(chunk_len, label="Training trajectory length", color="k", linestyle="--", linewidth=1.0)
    ax.get_legend().remove()
    
    # TODO: remember to order this correctly if new plots are added
axes[0, 0].legend(list(df_batch_avg.columns.unique("Network")) + [r"$T_{minibatch}$"], loc="upper left")
axes[1, -2].legend(list(df_batch_avg[df.columns.unique("Body")[-1]].columns.unique("Network")) + [r"$T_{minibatch}$"], loc="upper right")
axes[1, -1].legend(list(df_batch_avg[df.columns.unique("Body")[-1]].columns.unique("Network")) + [r"$T_{minibatch}$"], loc="upper right")
axes[0, 0].set(ylabel=f"Absolute rel. err. in true energy")
axes[1, 0].set(ylabel=f"Absolute rel. err. in true energy")
axes[1, 0].set(xlabel=f"Forward prediction (seconds)")
axes[1, 1].set(xlabel=f"Forward prediction (seconds)")
axes[1, 2].set(xlabel=f"Forward prediction (seconds)")
fig.tight_layout()

In [20]:
fig.savefig("energy-conservation.pdf", bbox_inches="tight")